In [1]:
import pandas as pd 
from umap import UMAP
from hdbscan import HDBSCAN
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import CountVectorizer
 
from bertopic import BERTopic
from bertopic.representation import KeyBERTInspired
from bertopic.vectorizers import ClassTfidfTransformer

from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
import nltk 
from nltk.corpus import wordnet
from nltk.tokenize import TreebankWordTokenizer
from nltk.corpus import stopwords


nltk.download('wordnet')
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
nltk.download('stopwords')

/opt/conda/envs/EHmin/lib/python3.9/site-packages/umap/distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/opt/conda/envs/EHmin/lib/python3.9/site-packages/umap/distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/opt/conda/envs/EHmin/lib/python3.9/site-packages/umap/distances.py:1086: NumbaDeprecationWarning:

True

In [2]:
df = pd.read_csv("vision_combined.csv")

print(df)

     Publication Type                                            Authors   
0                   C  Liu, Z; Lin, YT; Cao, Y; Hu, H; Wei, YX; Zhang...  \
1                   C  Touvron, H; Cord, M; Douze, M; Massa, F; Sabla...   
2                   J  Minaee, S; Boykov, YY; Porikli, F; Plaza, AJ; ...   
3                   J  Gao, SH; Cheng, MM; Zhao, K; Zhang, XY; Yang, ...   
4                   J  Guo, YL; Wang, HY; Hu, QY; Liu, H; Liu, L; Ben...   
...               ...                                                ...   
4995                C  Zhang, QR; Zuo, SM; Liang, C; Bukharin, A; He,...   
4996                C                        Zheng, L; Pan, HJ; Kong, LP   
4997                C     Yang, J; Chen, TC; Qin, F; Lam, MS; Landay, JA   
4998                C                      Lee, S; Yi, E; Lee, J; Kim, J   
4999                C                 Mascaro, EV; Ma, S; Ahn, H; Lee, D   

      Book Authors                                       Book Editors   
0             

In [3]:
df = df[["Article Title","Abstract"]]

# Initial Docs

In [4]:
docs = df["Abstract"].astype(str).tolist()
docs

['This paper presents a new vision Transformer, called Swin Transformer, that capably serves as a general-purpose backbone for computer vision. Challenges in adapting Transformer from language to vision arise from differences between the two domains, such as large variations in the scale of visual entities and the high resolution of pixels in images compared to words in text. To address these differences, we propose a hierarchical Transformer whose representation is computed with Shifted windows. The shifted windowing scheme brings greater efficiency by limiting self-attention computation to non-overlapping local windows while also allowing for cross-window connection. This hierarchical architecture has the flexibility to model at various scales and has linear computational complexity with respect to image size. These qualities of Swin Transformer make it compatible with a broad range of vision tasks, including image classification (87.3 top-1 accuracy on ImageNet-1K) and dense predict

# Change to uppercase and lowercase letters

In [5]:
for i in range(len(docs)):
    docs[i] = docs[i].lower()

# in counter vectorizer >> do lower transform, and removing stop words But it can effect on Embeding too 

In [6]:
docs

['this paper presents a new vision transformer, called swin transformer, that capably serves as a general-purpose backbone for computer vision. challenges in adapting transformer from language to vision arise from differences between the two domains, such as large variations in the scale of visual entities and the high resolution of pixels in images compared to words in text. to address these differences, we propose a hierarchical transformer whose representation is computed with shifted windows. the shifted windowing scheme brings greater efficiency by limiting self-attention computation to non-overlapping local windows while also allowing for cross-window connection. this hierarchical architecture has the flexibility to model at various scales and has linear computational complexity with respect to image size. these qualities of swin transformer make it compatible with a broad range of vision tasks, including image classification (87.3 top-1 accuracy on imagenet-1k) and dense predict

# Tockenization

In [7]:
tokenizer = TreebankWordTokenizer()

for i in range(len(docs)):
    docs[i] = " ".join(tokenizer.tokenize(docs[i]))

In [8]:
docs

['this paper presents a new vision transformer , called swin transformer , that capably serves as a general-purpose backbone for computer vision. challenges in adapting transformer from language to vision arise from differences between the two domains , such as large variations in the scale of visual entities and the high resolution of pixels in images compared to words in text. to address these differences , we propose a hierarchical transformer whose representation is computed with shifted windows. the shifted windowing scheme brings greater efficiency by limiting self-attention computation to non-overlapping local windows while also allowing for cross-window connection. this hierarchical architecture has the flexibility to model at various scales and has linear computational complexity with respect to image size. these qualities of swin transformer make it compatible with a broad range of vision tasks , including image classification ( 87.3 top-1 accuracy on imagenet-1k ) and dense 

# POS Tagging & Lammatization

In [9]:
def get_wordnet_pos(treebank_tag):
    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return None

In [10]:
tokenizer = TreebankWordTokenizer()

a = tokenizer.tokenize(docs[0])
" ".join(a)

'this paper presents a new vision transformer , called swin transformer , that capably serves as a general-purpose backbone for computer vision. challenges in adapting transformer from language to vision arise from differences between the two domains , such as large variations in the scale of visual entities and the high resolution of pixels in images compared to words in text. to address these differences , we propose a hierarchical transformer whose representation is computed with shifted windows. the shifted windowing scheme brings greater efficiency by limiting self-attention computation to non-overlapping local windows while also allowing for cross-window connection. this hierarchical architecture has the flexibility to model at various scales and has linear computational complexity with respect to image size. these qualities of swin transformer make it compatible with a broad range of vision tasks , including image classification ( 87.3 top-1 accuracy on imagenet-1k ) and dense p

## Test  Effect

In [11]:
lemmatizer = WordNetLemmatizer()
a = docs[0].split(" ")

print(a)
print([lemmatizer.lemmatize(word) for word in a])
tokens = word_tokenize(docs[0])
print([lemmatizer.lemmatize(word[0],pos = get_wordnet_pos(word[1])) if get_wordnet_pos(word[1]) else word[0]  for word in nltk.pos_tag(tokens)])

['this', 'paper', 'presents', 'a', 'new', 'vision', 'transformer', ',', 'called', 'swin', 'transformer', ',', 'that', 'capably', 'serves', 'as', 'a', 'general-purpose', 'backbone', 'for', 'computer', 'vision.', 'challenges', 'in', 'adapting', 'transformer', 'from', 'language', 'to', 'vision', 'arise', 'from', 'differences', 'between', 'the', 'two', 'domains', ',', 'such', 'as', 'large', 'variations', 'in', 'the', 'scale', 'of', 'visual', 'entities', 'and', 'the', 'high', 'resolution', 'of', 'pixels', 'in', 'images', 'compared', 'to', 'words', 'in', 'text.', 'to', 'address', 'these', 'differences', ',', 'we', 'propose', 'a', 'hierarchical', 'transformer', 'whose', 'representation', 'is', 'computed', 'with', 'shifted', 'windows.', 'the', 'shifted', 'windowing', 'scheme', 'brings', 'greater', 'efficiency', 'by', 'limiting', 'self-attention', 'computation', 'to', 'non-overlapping', 'local', 'windows', 'while', 'also', 'allowing', 'for', 'cross-window', 'connection.', 'this', 'hierarchical'

In [12]:
lemmatizer = WordNetLemmatizer()
tokenizer = TreebankWordTokenizer()

for i in range(len(docs)):
    tokens = word_tokenize(docs[i])
    docs[i] = " ".join([lemmatizer.lemmatize(word[0],pos = get_wordnet_pos(word[1])) if get_wordnet_pos(word[1]) else word[0]  for word in nltk.pos_tag(tokens)])

In [13]:
docs

['this paper present a new vision transformer , call swin transformer , that capably serve as a general-purpose backbone for computer vision . challenge in adapt transformer from language to vision arise from difference between the two domain , such as large variation in the scale of visual entity and the high resolution of pixel in image compare to word in text . to address these difference , we propose a hierarchical transformer whose representation be compute with shifted window . the shifted windowing scheme bring great efficiency by limit self-attention computation to non-overlapping local window while also allow for cross-window connection . this hierarchical architecture have the flexibility to model at various scale and have linear computational complexity with respect to image size . these quality of swin transformer make it compatible with a broad range of vision task , include image classification ( 87.3 top-1 accuracy on imagenet-1k ) and dense prediction task such as objec

# Remove Stop words

In [14]:
stop_words = set(stopwords.words('english')) 

for i in range(len(docs)):
    word_tockens = word_tokenize(docs[i])
    result =[]
    for word in word_tockens:
        if word not in stop_words:
            result.append(word)
    docs[i] = " ".join(result)


In [15]:
docs

['paper present new vision transformer , call swin transformer , capably serve general-purpose backbone computer vision . challenge adapt transformer language vision arise difference two domain , large variation scale visual entity high resolution pixel image compare word text . address difference , propose hierarchical transformer whose representation compute shifted window . shifted windowing scheme bring great efficiency limit self-attention computation non-overlapping local window also allow cross-window connection . hierarchical architecture flexibility model various scale linear computational complexity respect image size . quality swin transformer make compatible broad range vision task , include image classification ( 87.3 top-1 accuracy imagenet-1k ) dense prediction task object detection ( 58.7 box ap 51.1 mask ap coco test-dev ) semantic segmentation ( 53.5 miou ade20k val ) . performance surpass previous state-of-the-art large margin +2.7 box ap +2.6 mask ap coco , +3.2 mio

# MODEL

In [193]:
embedding_model = SentenceTransformer("all-MiniLM-L6-v2")
umap_model = UMAP(n_neighbors=15, n_components=5, min_dist=0.0, metric='cosine')
hdbscan_model = HDBSCAN(min_cluster_size=15, metric='euclidean', cluster_selection_method='eom', prediction_data=True)
vectorizer_model = CountVectorizer(stop_words=["image", "use", "model", "network", "computer", "vision"])
#"image", "use", "model", "method", "propose","computer","vision","network"
ctfidf_model = ClassTfidfTransformer()

In [194]:
model = BERTopic(
  embedding_model=embedding_model,        
  umap_model=umap_model,               
  hdbscan_model=hdbscan_model,              
  vectorizer_model=vectorizer_model, 
  ctfidf_model=ctfidf_model,
  nr_topics=50,
  n_gram_range=(1,2)       
)


In [195]:
topics, probabilities = model.fit_transform(docs)

In [196]:
topic_df = model.get_topic_info()
topic_df

Topic  Count                                         Name
0      -1   1348              -1_method_learning_propose_deep
1       0    303              0_action_human_pose_recognition
2       1    288                    1_plant_disease_leaf_crop
3       2    287            2_object_track_tracking_detection
4       3    178               3_crack_damage_concrete_bridge
5       4    158             4_facial_face_expression_emotion
6       5    134        5_defect_inspection_surface_detection
7       6    132               6_vehicle_traffic_system_plate
8       7    124          7_semantic_label_supervised_texture
9       8    121            8_cnns_accelerator_filter_pruning
10      9    113                 9_hand_gesture_sign_language
11     10    101   10_attack_adversarial_example_perturbation
12     11     95       11_anomaly_surveillance_event_abnormal
13     12     83          12_cancer_tumor_segmentation_tissue
14     13     83                        13_covid_19_chest_ray
15     14     78               14_point_cloud_registration_3d
16     15     74       15_edge_segmentation_algorithm_contour
17     16     72    16_text_character_handwritten_recognition
18     17     70             17_haze_dehazing_hazy_visibility
19     18     64         18_caption_captioning_video_language
20     19     63           19_gan_gans_generative_translation
21     20     63        20_light_enhancement_low_illumination
22     21     60            21_3d_shape_reconstruction_object
23     22     60          22_depth_estimation_monocular_kitti
24     23     54        23_underwater_fish_aquaculture_marine
25     24     54           24_dr_diabetic_retinopathy_retinal
26     25     49  25_background_foreground_video_segmentation
27     26     47            26_matrix_cluster_view_clustering
28     27     46                         27_person_re_id_reid
29     28     44             28_drone_aerial_object_detection
30     29     44                29_driver_gaze_eye_drowsiness
31     30     44             30_rain_streak_deraining_removal
32     31     44           31_transformer_attention_token_vit
33     32     42           32_domain_adaptation_target_source
34     33     38                33_search_nas_architecture_na
35     34     33            34_player_sport_action_basketball
36     35     33    35_pedestrian_attribute_detection_feature
37     36     32              36_crowd_counting_density_count
38     37     29            37_remote_sense_sensing_satellite
39     38     24                38_vqa_question_answer_visual
40     39     23            39_ship_vessel_maritime_detection
41     40     21                      40_age_face_gender_race
42     41     20          41_attention_channel_self_mechanism
43     42     20                   42_sketch_color_photo_sbir
44     43     19  43_distillation_knowledge_teacher_continual
45     44     19       44_surgical_instrument_surgery_surgeon
46     45     18             45_layer_cnn_function_activation
47     46     18         46_few_shot_classification_prototype
48     47     18   47_explanation_xai_uncertainty_explainable
49     48     15             48_glaucoma_optic_disc_diagnosis

In [197]:
get_topic = model.get_topic
get_topic(3)

[('crack', 0.06943115354927179),
 ('damage', 0.0467755510972798),
 ('concrete', 0.027045649703109985),
 ('bridge', 0.02164480194467404),
 ('pavement', 0.019770800647701436),
 ('detection', 0.01790510205559515),
 ('road', 0.017901637963023343),
 ('inspection', 0.016795284785169774),
 ('building', 0.01538481348910292),
 ('structural', 0.01467444199638918)]

In [198]:
zero=[]
number=[]
for i in range(len(topic_df)):
  zero.append('0')
  number.append(i-1)

topic_word_df=pd.DataFrame({
    'topic_num':number,
    'topic':topic_df['Name'],
    'w1':zero,
    'w2':zero,
    'w3':zero,
    'w4':zero,
    'w5':zero,
    'w6':zero,
    'w7':zero,
    'w8':zero,
    'w9':zero,
    'w10':zero
})

# 각 토픽별 10개 단어 정리
col = topic_word_df.columns
for i in range(len(topic_word_df)):
  for j in range(10):
    topic_word_df[col[j+2]][i]=get_topic(i-1)[j][0]

In [199]:
topic_word_df

topic_num                                        topic            w1   
0          -1              -1_method_learning_propose_deep        method  \
1           0              0_action_human_pose_recognition        action   
2           1                    1_plant_disease_leaf_crop         plant   
3           2            2_object_track_tracking_detection        object   
4           3               3_crack_damage_concrete_bridge         crack   
5           4             4_facial_face_expression_emotion        facial   
6           5        5_defect_inspection_surface_detection        defect   
7           6               6_vehicle_traffic_system_plate       vehicle   
8           7          7_semantic_label_supervised_texture      semantic   
9           8            8_cnns_accelerator_filter_pruning          cnns   
10          9                 9_hand_gesture_sign_language          hand   
11         10   10_attack_adversarial_example_perturbation        attack   
12         11       11_anomaly_surveillance_event_abnormal       anomaly   
13         12          12_cancer_tumor_segmentation_tissue        cancer   
14         13                        13_covid_19_chest_ray         covid   
15         14               14_point_cloud_registration_3d         point   
16         15       15_edge_segmentation_algorithm_contour          edge   
17         16    16_text_character_handwritten_recognition          text   
18         17             17_haze_dehazing_hazy_visibility          haze   
19         18         18_caption_captioning_video_language       caption   
20         19           19_gan_gans_generative_translation           gan   
21         20        20_light_enhancement_low_illumination         light   
22         21            21_3d_shape_reconstruction_object            3d   
23         22          22_depth_estimation_monocular_kitti         depth   
24         23        23_underwater_fish_aquaculture_marine    underwater   
25         24           24_dr_diabetic_retinopathy_retinal            dr   
26         25  25_background_foreground_video_segmentation    background   
27         26            26_matrix_cluster_view_clustering        matrix   
28         27                         27_person_re_id_reid        person   
29         28             28_drone_aerial_object_detection         drone   
30         29                29_driver_gaze_eye_drowsiness        driver   
31         30             30_rain_streak_deraining_removal          rain   
32         31           31_transformer_attention_token_vit   transformer   
33         32           32_domain_adaptation_target_source        domain   
34         33                33_search_nas_architecture_na        search   
35         34            34_player_sport_action_basketball        player   
36         35    35_pedestrian_attribute_detection_feature    pedestrian   
37         36              36_crowd_counting_density_count         crowd   
38         37            37_remote_sense_sensing_satellite        remote   
39         38                38_vqa_question_answer_visual           vqa   
40         39            39_ship_vessel_maritime_detection          ship   
41         40                      40_age_face_gender_race           age   
42         41          41_attention_channel_self_mechanism     attention   
43         42                   42_sketch_color_photo_sbir        sketch   
44         43  43_distillation_knowledge_teacher_continual  distillation   
45         44       44_surgical_instrument_surgery_surgeon      surgical   
46         45             45_layer_cnn_function_activation         layer   
47         46         46_few_shot_classification_prototype           few   
48         47   47_explanation_xai_uncertainty_explainable   explanation   
49         48             48_glaucoma_optic_disc_diagnosis      glaucoma   

              w2              w3            w4              w5            w6   
0       learning         propose          deep 

In [200]:
model.get_document_info(docs)

Document  Topic   
0     paper present new vision transformer , call sw...     31  \
1     recently , neural network purely base attentio...     31   
2     image segmentation key task computer vision im...     -1   
3     represent feature multiple scale great importa...     -1   
4     point cloud learning lately attract increase a...     14   
...                                                 ...    ...   
4995  large transformer-based model exhibit superior...     31   
4996  transformer architecture central sequence mode...     31   
4997  full-body tracking virtual reality improve pre...      9   
4998  depth completion task aim predict dense depth ...     -1   
4999  comprehend human motion fundamental challenge ...      0   

                                    Name   
0     31_transformer_attention_token_vit  \
1     31_transformer_attention_token_vit   
2        -1_method_learning_propose_deep   
3        -1_method_learning_propose_deep   
4         14_point_cloud_registration_3d   
...                                  ...   
4995  31_transformer_attention_token_vit   
4996  31_transformer_attention_token_vit   
4997        9_hand_gesture_sign_language   
4998     -1_method_learning_propose_deep   
4999     0_action_human_pose_recognition   

                                            Top_n_words  Probability   
0     transformer - attention - token - vit - task -...     1.000000  \
1     transformer - attention - token - vit - task -...     0.783058   
2     method - learning - propose - deep - data - fe...     0.000000   
3     method - learning - propose - deep - data - fe...     0.000000   
4     point - cloud - registration - 3d - lidar - lo...     1.000000   
...                                                 ...          ...   
4995  transformer - attention - token - vit - task -...     0.708527   
4996  transformer - attention - token - vit - task -...     0.749345   
4997  hand - gesture - sign - language - recognition...     0.221672   
4998  method - learning - propose - deep - data - fe...     0.000000   
4999  action - human - pose - recognition - activity...     0.299867   

      Representative_document  
0                       False  
1                       False  
2                       False  
3                       False  
4                        True  
...                       ...  
4995                    False  
4996                    False  
4997                    False  
4998                    False  
4999                    False  

[5000 rows x 6 columns]

In [201]:
df = model.get_document_info(docs)
df = df[df['Topic'] == 9]
df["Document"]

df["Document"].to_csv('df_topic_9.txt', index=False)

In [202]:
model.visualize_barchart()

In [203]:
model.visualize_heatmap()

In [204]:
model.visualize_topics()